In [1]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import os
import optuna
# Suppress warnings
import warnings
warnings.filterwarnings("ignore")

In [2]:
target_cols = ["cohesion", "syntax", "vocabulary", "phraseology", "grammar", "conventions"] 


In [3]:
csvs1 = [
    "/kaggle/input/fb3-final-oofs/oof_files/exp01/microsoft-deberta-v3-base/oof_df.csv", 
    '/kaggle/input/fb3-final-oofs/oof_files/model23.csv', 
    '/kaggle/input/fb3-final-oofs/oof_files/0926-deberta-v3-large.csv', 
    '/kaggle/input/fb3-final-oofs/oof_files/nischay.csv',
    '/kaggle/input/fb3-final-oofs/oof_files/0919-deberta-v2-xlarge-mnli.csv', 
    "/kaggle/input/fb3-final-oofs/oof_files/exp14/roberta-large/oof_df.csv", 
    '/kaggle/input/fb3-final-oofs/oof_files/0911-deberta-v3-large.csv', 
    "/kaggle/input/fb3-final-oofs/oof_files/exp13/microsoft-deberta-v3-large/oof_df.csv", 
    "/kaggle/input/fb3-final-oofs/oof_files/exp02/distilbert-base-uncased/oof_df.csv", 
    "/kaggle/input/fb3-final-oofs/oof_files/model52.csv",
    "/kaggle/input/fb3-final-oofs/oof_files/exp01/microsoft-deberta-v3-base-pldf/oof_df.csv", # 11
    "/kaggle/input/fb3-final-oofs/oof_files/exp11/roberta-large/oof_df.csv",
    '/kaggle/input/fb3-final-oofs/oof_files/model68.csv', 
    '/kaggle/input/fb3-final-oofs/oof_files/model70.csv',
    '/kaggle/input/fb3-final-oofs/oof_files/model71.csv', 
    '/kaggle/input/fb3-final-oofs/oof_files/fb3_embeddings/fb_bart_large_512_oof.csv',
    "/kaggle/input/fb3-final-oofs/oof_files/fb3_embeddings/ad_v3_roberta_large.csv",
    "/kaggle/input/fb3-final-oofs/oof_files/fb3_embeddings/fb_bart_large_mnli.csv",
]


In [4]:
len(csvs1)

18

In [5]:
import pandas as pd
import numpy as np
from sklearn.metrics import mean_squared_error

def MCRMSE(y_trues, y_preds):
    scores = []
    idxes = y_trues.shape[1]
    for i in range(idxes):
        y_true = y_trues[:,i]
        y_pred = y_preds[:,i]
        score = mean_squared_error(y_true, y_pred, squared=False) # RMSE
        scores.append(score)
    mcrmse_score = np.mean(scores)
    return mcrmse_score, scores



def MCRMSE_SINGLE(y_trues, y_preds):
    scores = []
    mcrmse_score = mean_squared_error(y_trues, y_preds, squared=False) # RMSE
    return mcrmse_score, scores



def get_score(y_trues, y_preds, single=False):
    if single:
        mcrmse_score, scores = MCRMSE_SINGLE(y_trues, y_preds)
    else:
        mcrmse_score, scores = MCRMSE(y_trues, y_preds)
    return mcrmse_score, scores


def minimize_rmse(params):
    preds = None
    for index, val in enumerate(params.keys()):
        if index == 0:
            preds = params[val]*all_preds[0]
        else:
            preds += params[val]*all_preds[index]
    
    
    param_sum = 0
    for key, val in params.items():
        param_sum += val

    preds = preds/param_sum

    
    score, scores = get_score(labels, preds) 
    return score


## cohesion

In [6]:
all_preds = []

target_cols = ["cohesion"]

labels = None
for index, csv in enumerate(csvs1):
    oof_df = pd.read_csv(csv)
    
    if index == 10:
        oof_df = oof_df.loc[~oof_df.pred_cohesion.isna()]

    oof_df = oof_df.sort_values('text_id').reset_index(drop=True)

    if index==0: 
        print(oof_df.shape)
        df = pd.read_csv(csvs1[0])
        df = df.sort_values('text_id').reset_index(drop=True)
        labels = df[target_cols].values
                
    if f"pred_{target_cols[0]}" in oof_df.columns:        
        preds = oof_df[[f"pred_{c}" for c in target_cols]].values
    else:
        preds = oof_df[target_cols].values
        
    all_preds.append(preds) 
    single=True
    scores = []
    if single:
        score = get_score(labels, preds, single=True)
    else:
        score, scores = get_score(labels, preds)
#     print(score, scores)
    
print("*"*100)
print()

def objective(trial):
    params = {}    
    for i in range(18):
        params[f"w{i+1}"] = trial.suggest_float(f'w{i+1}', 0, 1)  
        

    score = minimize_rmse(params)
    return score

study = optuna.create_study(direction='minimize')
study.optimize(objective, n_trials=2000)

cohesion_params = study.best_params

(3911, 16)


[I 2022-12-02 12:51:49,408] A new study created in memory with name: no-name-544ab246-b03e-47bf-bdd6-4dca9485d438
[I 2022-12-02 12:51:49,414] Trial 0 finished with value: 0.4695612903044436 and parameters: {'w1': 0.07045801775887484, 'w2': 0.9925860836146959, 'w3': 0.22076601834456355, 'w4': 0.8577431551481647, 'w5': 0.7180580556133245, 'w6': 0.11854908055745839, 'w7': 0.040059150788205544, 'w8': 0.4304395302355257, 'w9': 0.550193947177522, 'w10': 0.8517228667071212, 'w11': 0.6687553235811414, 'w12': 0.8812476463600825, 'w13': 0.8107977515948234, 'w14': 0.37634430304700284, 'w15': 0.1768695608294314, 'w16': 0.6544737488270761, 'w17': 0.3629536794488195, 'w18': 0.06266491718886746}. Best is trial 0 with value: 0.4695612903044436.
[I 2022-12-02 12:51:49,420] Trial 1 finished with value: 0.4709250784447476 and parameters: {'w1': 0.47270530849960213, 'w2': 0.46589897486931797, 'w3': 0.36788807425846004, 'w4': 0.671219437594127, 'w5': 0.16321849077910622, 'w6': 0.19169222317767354, 'w7': 0.

****************************************************************************************************



[I 2022-12-02 12:51:49,625] Trial 12 finished with value: 0.46958500083919424 and parameters: {'w1': 0.9172069666790946, 'w2': 0.20633551274044692, 'w3': 0.6561189280632161, 'w4': 0.25929462760688926, 'w5': 0.9096005667469184, 'w6': 0.9306672093149482, 'w7': 0.3178856416079996, 'w8': 0.9528633175683282, 'w9': 0.29507952813728655, 'w10': 0.9889437858006543, 'w11': 0.3722490510219827, 'w12': 0.3384864079348811, 'w13': 0.924491245900437, 'w14': 0.0038468593341374653, 'w15': 0.9487244187152478, 'w16': 0.618975016974138, 'w17': 0.015079672504933611, 'w18': 0.6380303419517728}. Best is trial 2 with value: 0.46927171983982185.
[I 2022-12-02 12:51:49,682] Trial 13 finished with value: 0.47068964208146274 and parameters: {'w1': 0.995361793012794, 'w2': 0.5528874242758195, 'w3': 0.0009912932310454092, 'w4': 0.3324233154553459, 'w5': 0.7380794240481148, 'w6': 0.7053137124113931, 'w7': 0.2799262164527242, 'w8': 0.17150401285851308, 'w9': 0.19985416167166992, 'w10': 0.012587542824871845, 'w11': 0.1

## syntax

In [7]:
all_preds = []

target_cols = ["syntax"]

labels = None
for index, csv in enumerate(csvs1):
    oof_df = pd.read_csv(csv)
    
    if index == 10:
        oof_df = oof_df.loc[~oof_df.pred_cohesion.isna()]

    oof_df = oof_df.sort_values('text_id').reset_index(drop=True)

    if index==0: 
        print(oof_df.shape)
        df = pd.read_csv(csvs1[0])
        df = df.sort_values('text_id').reset_index(drop=True)
        labels = df[target_cols].values
                
    if f"pred_{target_cols[0]}" in oof_df.columns:        
        preds = oof_df[[f"pred_{c}" for c in target_cols]].values
    else:
        preds = oof_df[target_cols].values
        
    all_preds.append(preds) 
    single=True
    scores = []
    if single:
        score = get_score(labels, preds, single=True)
    else:
        score, scores = get_score(labels, preds)
#     print(score, scores)
    
print("*"*100)
print()


def objective(trial):
    params = {}    
    for i in range(18):
        params[f"w{i+1}"] = trial.suggest_float(f'w{i+1}', 0, 1)  
        

    score = minimize_rmse(params)
    return score

study = optuna.create_study(direction='minimize')
study.optimize(objective, n_trials=2000)

syntax_params = study.best_params

(3911, 16)


[I 2022-12-02 12:58:21,383] A new study created in memory with name: no-name-1b31ef12-c23a-4dfd-9695-e6efb004a3ea
[I 2022-12-02 12:58:21,404] Trial 0 finished with value: 0.43776090368909415 and parameters: {'w1': 0.5999502639553319, 'w2': 0.5856124762801422, 'w3': 0.2848663310167324, 'w4': 0.26664072568074726, 'w5': 0.17857812595630573, 'w6': 0.24645663303747922, 'w7': 0.1479905984147022, 'w8': 0.13025915997322146, 'w9': 0.7133965595335542, 'w10': 0.5934724239707311, 'w11': 0.9181864058081501, 'w12': 0.10623170364813117, 'w13': 0.38232651408034024, 'w14': 0.7270698664217579, 'w15': 0.6230231775265488, 'w16': 0.49315349665264163, 'w17': 0.19325305278447147, 'w18': 0.5975460201112621}. Best is trial 0 with value: 0.43776090368909415.
[I 2022-12-02 12:58:21,410] Trial 1 finished with value: 0.4375312392034043 and parameters: {'w1': 0.9133025297653179, 'w2': 0.030807186094892303, 'w3': 0.0035790595921004753, 'w4': 0.06860998524853101, 'w5': 0.12679206269771304, 'w6': 0.2255464854039949, '

****************************************************************************************************



[I 2022-12-02 12:58:21,622] Trial 12 finished with value: 0.4371793688886594 and parameters: {'w1': 0.7401023043703645, 'w2': 0.7107566904176037, 'w3': 0.6615856169426004, 'w4': 0.9852120305093123, 'w5': 0.35015749113443506, 'w6': 0.02558766216011779, 'w7': 0.9160074598496787, 'w8': 0.37386774917888993, 'w9': 0.8588048335300686, 'w10': 0.026464265158333666, 'w11': 0.0029386680831104822, 'w12': 0.9923351835330125, 'w13': 0.2544142595495408, 'w14': 0.43414719812812264, 'w15': 0.2534476584379178, 'w16': 0.3304584549865791, 'w17': 0.024515941015632866, 'w18': 0.9851929826979113}. Best is trial 4 with value: 0.43695427646870233.
[I 2022-12-02 12:58:21,677] Trial 13 finished with value: 0.43735158513561617 and parameters: {'w1': 0.3640785589215239, 'w2': 0.34122281438965174, 'w3': 0.9946046812044873, 'w4': 0.5886978943903658, 'w5': 0.6445378478037335, 'w6': 0.5090823182810642, 'w7': 0.7358023755793799, 'w8': 0.6777869070083293, 'w9': 0.38036745159693564, 'w10': 0.3864531444592414, 'w11': 0.2

## vocabulary

In [8]:
all_preds = []

target_cols = ["vocabulary"]

labels = None
for index, csv in enumerate(csvs1):
    oof_df = pd.read_csv(csv)
    
    if index == 10:
        oof_df = oof_df.loc[~oof_df.pred_cohesion.isna()]

    oof_df = oof_df.sort_values('text_id').reset_index(drop=True)

    if index==0: 
        print(oof_df.shape)
        df = pd.read_csv(csvs1[0])
        df = df.sort_values('text_id').reset_index(drop=True)
        labels = df[target_cols].values
                
    if f"pred_{target_cols[0]}" in oof_df.columns:        
        preds = oof_df[[f"pred_{c}" for c in target_cols]].values
    else:
        preds = oof_df[target_cols].values
        
    all_preds.append(preds) 
    single=True
    scores = []
    if single:
        score = get_score(labels, preds, single=True)
    else:
        score, scores = get_score(labels, preds)
#     print(score, scores)
    
print("*"*100)
print()


def objective(trial):
    params = {}    
    for i in range(18):
        params[f"w{i+1}"] = trial.suggest_float(f'w{i+1}', 0, 1)  
        

    score = minimize_rmse(params)
    return score

study = optuna.create_study(direction='minimize')
study.optimize(objective, n_trials=2000)

vocabulary_params = study.best_params

(3911, 16)


[I 2022-12-02 13:04:55,530] A new study created in memory with name: no-name-06b7a94d-6f2a-4b87-85ee-1dcd6e31ac5e
[I 2022-12-02 13:04:55,552] Trial 0 finished with value: 0.4060246797703425 and parameters: {'w1': 0.8182759473062122, 'w2': 0.28910804602940665, 'w3': 0.09454371544492368, 'w4': 0.0074369630253696695, 'w5': 0.274160669881211, 'w6': 0.3743367838538749, 'w7': 0.09832793010276808, 'w8': 0.7057332278170957, 'w9': 0.5163013047289482, 'w10': 0.6839649423815538, 'w11': 0.9092580353447431, 'w12': 0.7441893562595876, 'w13': 0.014430981984941638, 'w14': 0.4299491247880757, 'w15': 0.4515710222432383, 'w16': 0.5337569936929973, 'w17': 0.1806784555149925, 'w18': 0.4270116800834747}. Best is trial 0 with value: 0.4060246797703425.
[I 2022-12-02 13:04:55,557] Trial 1 finished with value: 0.4072371419653959 and parameters: {'w1': 0.18373676586936016, 'w2': 0.5816995445235194, 'w3': 0.37613597490998496, 'w4': 0.7247014519224378, 'w5': 0.04849270487494972, 'w6': 0.8316729579082403, 'w7': 0.

****************************************************************************************************



[I 2022-12-02 13:04:55,765] Trial 12 finished with value: 0.40649095034620214 and parameters: {'w1': 0.015257180256950553, 'w2': 0.8634399666813258, 'w3': 0.19601519104712278, 'w4': 0.9914161039139372, 'w5': 0.7336098766727904, 'w6': 0.14126987695499776, 'w7': 0.9938762333136677, 'w8': 0.2574917545016554, 'w9': 0.35036145043527744, 'w10': 0.7775283964746701, 'w11': 0.44153584474832497, 'w12': 0.3432197159143052, 'w13': 0.42039077495961175, 'w14': 0.9679751786667894, 'w15': 0.29246301159208127, 'w16': 0.23735415705429913, 'w17': 0.024860547599171667, 'w18': 0.23232364965319247}. Best is trial 4 with value: 0.4057305916038496.
[I 2022-12-02 13:04:55,823] Trial 13 finished with value: 0.40607373413600406 and parameters: {'w1': 0.39772005115440134, 'w2': 0.8796720799507338, 'w3': 0.7047811239293457, 'w4': 0.007722357753815079, 'w5': 0.33035242692083056, 'w6': 0.9763371281271129, 'w7': 0.8764989667715019, 'w8': 0.024164268652889523, 'w9': 0.4743517259414686, 'w10': 0.5126868796354435, 'w11'

## phraseology

In [9]:
all_preds = []

target_cols = ["phraseology"]

labels = None
for index, csv in enumerate(csvs1):
    oof_df = pd.read_csv(csv)
    
    if index == 10:
        oof_df = oof_df.loc[~oof_df.pred_cohesion.isna()]

    oof_df = oof_df.sort_values('text_id').reset_index(drop=True)

    if index==0: 
        print(oof_df.shape)
        df = pd.read_csv(csvs1[0])
        df = df.sort_values('text_id').reset_index(drop=True)
        labels = df[target_cols].values
                
    if f"pred_{target_cols[0]}" in oof_df.columns:        
        preds = oof_df[[f"pred_{c}" for c in target_cols]].values
    else:
        preds = oof_df[target_cols].values
        
    all_preds.append(preds) 
    single=True
    scores = []
    if single:
        score = get_score(labels, preds, single=True)
    else:
        score, scores = get_score(labels, preds)
#     print(score, scores)
    
print("*"*100)
print()


def objective(trial):
    params = {}    
    for i in range(18):
        params[f"w{i+1}"] = trial.suggest_float(f'w{i+1}', 0, 1)  
        

    score = minimize_rmse(params)
    return score

study = optuna.create_study(direction='minimize')
study.optimize(objective, n_trials=2000)

phraseology_params = study.best_params

(3911, 16)


[I 2022-12-02 13:11:32,105] A new study created in memory with name: no-name-7dd35182-9199-46a9-9e46-eb73da523e80
[I 2022-12-02 13:11:32,127] Trial 0 finished with value: 0.44669924038073977 and parameters: {'w1': 0.8587832071101442, 'w2': 0.7379912376808331, 'w3': 0.3128559250262942, 'w4': 0.8766381335573331, 'w5': 0.30742765231477676, 'w6': 0.4120270137643799, 'w7': 0.6801955528612941, 'w8': 0.9751020791364152, 'w9': 0.5248803334877605, 'w10': 0.3147083105474602, 'w11': 0.07703585288254, 'w12': 0.7848153476755158, 'w13': 0.8557078520747847, 'w14': 0.03668599586957921, 'w15': 0.8746583846242633, 'w16': 0.8399633251591944, 'w17': 0.4461921258785255, 'w18': 0.5685692463447928}. Best is trial 0 with value: 0.44669924038073977.
[I 2022-12-02 13:11:32,132] Trial 1 finished with value: 0.44709397969931425 and parameters: {'w1': 0.892436573179865, 'w2': 0.23149896676720794, 'w3': 0.4970898801949838, 'w4': 0.457150388739768, 'w5': 0.6539233366910719, 'w6': 0.6947464334682694, 'w7': 0.09686177

****************************************************************************************************



[I 2022-12-02 13:11:32,332] Trial 12 finished with value: 0.44625853090064327 and parameters: {'w1': 0.5735462992943378, 'w2': 0.5682882508214117, 'w3': 0.443470464960031, 'w4': 0.6827791182626574, 'w5': 0.8415282245107092, 'w6': 0.2544752346098641, 'w7': 0.9955782988522027, 'w8': 0.7810266085968561, 'w9': 0.44466413195656024, 'w10': 0.9981157856803367, 'w11': 0.9774890611065764, 'w12': 0.197647821124591, 'w13': 0.4662483336036425, 'w14': 0.19387421608185096, 'w15': 0.29108090475191345, 'w16': 0.5441208791921465, 'w17': 0.08634905968707793, 'w18': 0.9969796047852808}. Best is trial 12 with value: 0.44625853090064327.
[I 2022-12-02 13:11:32,388] Trial 13 finished with value: 0.4462332772677336 and parameters: {'w1': 0.4626691605033689, 'w2': 0.5790836773122919, 'w3': 0.6357909506792028, 'w4': 0.6829389597244829, 'w5': 0.7790116245184073, 'w6': 0.007437602636179486, 'w7': 0.9804617205710352, 'w8': 0.5166333475649815, 'w9': 0.47789882899182984, 'w10': 0.9721064260572366, 'w11': 0.79052588

## grammar

In [10]:
all_preds = []

target_cols = ["grammar"]

labels = None
for index, csv in enumerate(csvs1):
    oof_df = pd.read_csv(csv)
    
    if index == 10:
        oof_df = oof_df.loc[~oof_df.pred_cohesion.isna()]

    oof_df = oof_df.sort_values('text_id').reset_index(drop=True)

    if index==0: 
        print(oof_df.shape)
        df = pd.read_csv(csvs1[0])
        df = df.sort_values('text_id').reset_index(drop=True)
        labels = df[target_cols].values
                
    if f"pred_{target_cols[0]}" in oof_df.columns:        
        preds = oof_df[[f"pred_{c}" for c in target_cols]].values
    else:
        preds = oof_df[target_cols].values
        
    all_preds.append(preds) 
    single=True
    scores = []
    if single:
        score = get_score(labels, preds, single=True)
    else:
        score, scores = get_score(labels, preds)
#     print(score, scores)
    
print("*"*100)
print()


def objective(trial):
    params = {}    
    for i in range(18):
        params[f"w{i+1}"] = trial.suggest_float(f'w{i+1}', 0, 1)  
        

    score = minimize_rmse(params)
    return score

study = optuna.create_study(direction='minimize')
study.optimize(objective, n_trials=2000)

grammar_params = study.best_params

(3911, 16)


[I 2022-12-02 13:18:12,011] A new study created in memory with name: no-name-9c6d6014-4ba5-48f8-8e36-26df75bf37c4
[I 2022-12-02 13:18:12,032] Trial 0 finished with value: 0.4624107792531632 and parameters: {'w1': 0.775115986980571, 'w2': 0.3926771435766182, 'w3': 0.3894286270986713, 'w4': 0.5408802866274133, 'w5': 0.38470007511595605, 'w6': 0.5075076538358422, 'w7': 0.30437167914090923, 'w8': 0.21505034455537253, 'w9': 0.648880743905375, 'w10': 0.12410928498537577, 'w11': 0.4436606316052826, 'w12': 0.01493030799123285, 'w13': 0.1453917598587562, 'w14': 0.7654065895595306, 'w15': 0.8967636367167745, 'w16': 0.40519084185942733, 'w17': 0.2266782026919989, 'w18': 0.28349555018117933}. Best is trial 0 with value: 0.4624107792531632.
[I 2022-12-02 13:18:12,037] Trial 1 finished with value: 0.46261996445746784 and parameters: {'w1': 0.6166098549939784, 'w2': 0.056281682861490046, 'w3': 0.7037897772805768, 'w4': 0.9478505424673106, 'w5': 0.11912607350958215, 'w6': 0.44566500015161203, 'w7': 0.

****************************************************************************************************



[I 2022-12-02 13:18:12,237] Trial 12 finished with value: 0.4610938635954986 and parameters: {'w1': 0.9605678984344422, 'w2': 0.9733067913101916, 'w3': 0.31046519178498905, 'w4': 0.23901910558249756, 'w5': 0.7462323245613168, 'w6': 0.738603441311371, 'w7': 0.9614828362220285, 'w8': 0.976501482823194, 'w9': 0.27162347881076354, 'w10': 0.6941129475730564, 'w11': 0.9991675525256072, 'w12': 0.9588597604713442, 'w13': 0.7514256584150283, 'w14': 0.15128062492083733, 'w15': 0.5469833027741428, 'w16': 0.9601776626205534, 'w17': 0.259048986523583, 'w18': 0.0038386046503006144}. Best is trial 12 with value: 0.4610938635954986.
[I 2022-12-02 13:18:12,294] Trial 13 finished with value: 0.4616886495050785 and parameters: {'w1': 0.9861900522256184, 'w2': 0.7482509323919828, 'w3': 0.15087674412464985, 'w4': 0.20017095946873076, 'w5': 0.7637742679061709, 'w6': 0.9989866290695169, 'w7': 0.9909478446469623, 'w8': 0.9175198125040093, 'w9': 0.2139886951341409, 'w10': 0.992094494078261, 'w11': 0.7763134112

## conventions

In [11]:
all_preds = []

target_cols = ["conventions"]

labels = None
for index, csv in enumerate(csvs1):
    oof_df = pd.read_csv(csv)
    
    if index == 10:
        oof_df = oof_df.loc[~oof_df.pred_cohesion.isna()]

    oof_df = oof_df.sort_values('text_id').reset_index(drop=True)

    if index==0: 
        print(oof_df.shape)
        df = pd.read_csv(csvs1[0])
        df = df.sort_values('text_id').reset_index(drop=True)
        labels = df[target_cols].values
                
    if f"pred_{target_cols[0]}" in oof_df.columns:        
        preds = oof_df[[f"pred_{c}" for c in target_cols]].values
    else:
        preds = oof_df[target_cols].values
        
    all_preds.append(preds) 
    single=True
    scores = []
    if single:
        score = get_score(labels, preds, single=True)
    else:
        score, scores = get_score(labels, preds)
#     print(score, scores)
    
print("*"*100)
print()


def objective(trial):
    params = {}    
    for i in range(18):
        params[f"w{i+1}"] = trial.suggest_float(f'w{i+1}', 0, 1)  
        

    score = minimize_rmse(params)
    return score

study = optuna.create_study(direction='minimize')
study.optimize(objective, n_trials=2000)

conventions_params = study.best_params

(3911, 16)


[I 2022-12-02 13:24:46,975] A new study created in memory with name: no-name-d631f8ce-fda6-426a-9dee-9085c91227ac
[I 2022-12-02 13:24:46,997] Trial 0 finished with value: 0.4359246371495251 and parameters: {'w1': 0.8063132902861905, 'w2': 0.7931829723807747, 'w3': 0.9297986677968927, 'w4': 0.35474556597362283, 'w5': 0.11365717613116, 'w6': 0.5137722521678503, 'w7': 0.06272722869193825, 'w8': 0.10572091484833412, 'w9': 0.928794566681727, 'w10': 0.04562128729797732, 'w11': 0.6315377205457475, 'w12': 0.4403213696219982, 'w13': 0.17420273050767587, 'w14': 0.06930036852497268, 'w15': 0.49159049049341974, 'w16': 0.4001577438227114, 'w17': 0.7233888956529609, 'w18': 0.20881649023257154}. Best is trial 0 with value: 0.4359246371495251.
[I 2022-12-02 13:24:47,002] Trial 1 finished with value: 0.43656914453607215 and parameters: {'w1': 0.4296699005780047, 'w2': 0.5828524683714377, 'w3': 0.6435388922045021, 'w4': 0.6312365547295105, 'w5': 0.9863276021052586, 'w6': 0.5192389333411728, 'w7': 0.5327

****************************************************************************************************



[I 2022-12-02 13:24:47,212] Trial 12 finished with value: 0.4348562459029637 and parameters: {'w1': 0.6837540211485402, 'w2': 0.6373279237694088, 'w3': 0.30237890264953443, 'w4': 0.9166630373264495, 'w5': 0.6215108252170479, 'w6': 0.9888215279443306, 'w7': 0.3036617003260995, 'w8': 0.3048921332009575, 'w9': 0.021090105668772813, 'w10': 0.6398517437993874, 'w11': 0.8129645971350012, 'w12': 0.7025505748995429, 'w13': 0.9731139616905301, 'w14': 0.6138168855739042, 'w15': 0.21329606729191128, 'w16': 0.03044497626745163, 'w17': 0.42174990857181893, 'w18': 0.3563701867446091}. Best is trial 12 with value: 0.4348562459029637.
[I 2022-12-02 13:24:47,269] Trial 13 finished with value: 0.43508823083994536 and parameters: {'w1': 0.6531169025351165, 'w2': 0.5420914989935814, 'w3': 0.2807740551977894, 'w4': 0.023675059078363758, 'w5': 0.6395107368581524, 'w6': 0.9829299301275204, 'w7': 0.35552597276996045, 'w8': 0.4026927786059945, 'w9': 0.00299088889920943, 'w10': 0.3006436776028662, 'w11': 0.3936

## Final OOF Score

In [12]:
all_preds = []

target_cols = ["cohesion", "syntax", "vocabulary", "phraseology", "grammar", "conventions"] 

labels = None
for index, csv in enumerate(csvs1):
    oof_df = pd.read_csv(csv)
    
    if index == 10:
        oof_df = oof_df.loc[~oof_df.pred_cohesion.isna()]

    oof_df = oof_df.sort_values('text_id').reset_index(drop=True)

    if index==0: 
        print(oof_df.shape)
        df = pd.read_csv(csvs1[0])
        df = df.sort_values('text_id').reset_index(drop=True)
        labels = df[target_cols].values
                
    if f"pred_{target_cols[0]}" in oof_df.columns:        
        preds = oof_df[[f"pred_{c}" for c in target_cols]].values
    else:
        preds = oof_df[target_cols].values
        
    all_preds.append(preds) 
    single=False
    scores = []
    if single:
        score = get_score(labels, preds, single=True)
    else:
        score, scores = get_score(labels, preds)
    
print("*"*100)
print()

(3911, 16)
****************************************************************************************************



In [13]:
params_arr = [
    cohesion_params, syntax_params, vocabulary_params, phraseology_params, grammar_params, conventions_params
]

final_preds = np.zeros((all_preds[0].shape[0], all_preds[0].shape[1]))
target_cols=['cohesion', 'syntax', 'vocabulary', 'phraseology', 'grammar', 'conventions']

for idx, val in enumerate(target_cols):
    params = params_arr[idx]
    preds = None
    for index, val in enumerate(params.keys()):
        if index == 0:
            preds = params[val]*all_preds[0][:, idx]
        else:
            preds += params[val]*all_preds[index][:, idx]
    
    param_sum = 0
    for key, val in params.items():
        param_sum += val
    
    preds = preds/param_sum    
    final_preds[:, idx] = preds
    
    


In [14]:
score, scores = get_score(labels, final_preds) 
print(score, scores)

0.4412382973790457 [0.46739676181067846, 0.4362888427297585, 0.404826361122737, 0.4457427231429181, 0.45949856300943637, 0.433676532458746]


## Best Params [Obtained with further finetuning]

In [15]:
cohesion_params = {
'w1': 0.0,
'w2': 0.5339168335555392,
'w3': 0.09485748176049003,
'w4': 0.0,
'w5': 0.14303593671645293,
'w6': 0.0047626000496182605,
'w7': 0.23954608346995007,
'w8': 0.0,
'w9': 0.0,
'w10': 0.8311532588851793,
'w11': 0.0,
'w12': 0.26863755221859564,
'w13': 0.0,
'w14': 0.0,
'w15': 0.31710470634309795, 
'w16': 0.0,
'w17': 0.1301660809650191,
'w18': 0.26218740851868694,
}


syntax_params = {
'w1': 0.0,
'w2': 0.8451958942855791,
'w3': 0.2459414460433332,
'w4': 0.4520446477445495,
'w5': 0.20418651230539753,
'w6': 0.08672594949747597,
'w7': 0.15391987575006652,
'w8': 0.11321219092387992,
'w9': 0.17602176995308577,
'w10': 0.0,
'w11': 0.2152036803178686,
'w12': 0.3099961420524598,
'w13': 0.13666917267095344,
'w14': 0.0,
'w15': 0.0,
'w16': 0.0,
'w17': 0.05033577777117823,
'w18': 0.0,
}


vocabulary_params = {
'w1': 0.0,
'w2': 0.9773458049522954,
'w3': 0.2701026066781923,
'w4': 0.0897421465007397,
'w5': 0.15896833762261456,
'w6': 0.0,
'w7': 0.2928413082942847,
'w8': 0.0,
'w9':  0.0,
'w10': 0.0,
'w11': 0.8767428775546303,
'w12': 0.4726624864147732,
'w13': 0.0,
'w14': 0.0,
'w15': 0.0,
'w16': 0.25172049707419175,
'w17': 0.0,
'w18': 0.40482373123677484,
}



phraseology_params = {
'w1': 0.392685735091344,
'w2': 0.3070567674390591,
'w3': 0.3462181341249304,
'w4': 0.17041942610869798,
'w5': 0.14481112060204787,
'w6': 0.0,
'w7': 0.2599596290500239,
'w8': 0.10539019715985688,
'w9': 0.16984818297705645,
'w10': 0.0,
'w11': 0.6418791957661959,
'w12': 0.08624376314860029,
'w13': 0.11344585964552807,
'w14': 0.0,
'w15': 0.0010443799298908965,
'w16': 0.0,
'w17': 0.08623753880879229,
'w18': 0.11955178842328568,
}


grammar_params = {
'w1': 0.14958952407952508,
'w2': 0.6647186203882494,
'w3': 0.449548924059724,
'w4': 0.0,
'w5': 0.0,
'w6': 0.0,
'w7': 0.17948357028693315,
'w8': 0.19411977625456364,
'w9':  0.0,
'w10': 0.6059328388312332,
'w11': 0.9999991120158438,
'w12': 0.2802250949790587,
'w13': 0.0,
'w14': 0.5641886830643286,
'w15': 0.9366227900298044,  
'w16': 0.0,
'w17': 0.0,
'w18': 0.0
}



conventions_params = {
'w1': 0.5408619674998405,
'w2': 0.7553072761106709,
'w3': 0.0,
'w4': 0.09078051730409513,
'w5': 0.09671915329098137,
'w6': 0.11039775351155291,
'w7': 0.004386647001662398,
'w8': 0.0,
'w9':  0.0,
'w10': 0.48620313439658697,
'w11': 0.22047198209216726,
'w12': 0.09552947797827362,
'w13': 0.2379674258891966,
'w14': 0.0,
'w15': 0.0,  
'w16': 0.02313623151682687,
'w17': 0.15807586514371233,
'w18': 0.0
}

In [16]:
params_arr = [
    cohesion_params, syntax_params, vocabulary_params, phraseology_params, grammar_params, conventions_params
]

final_preds = np.zeros((all_preds[0].shape[0], all_preds[0].shape[1]))
target_cols=['cohesion', 'syntax', 'vocabulary', 'phraseology', 'grammar', 'conventions']

for idx, val in enumerate(target_cols):
    params = params_arr[idx]
    preds = None
    for index, val in enumerate(params.keys()):
        if index == 0:
            preds = params[val]*all_preds[0][:, idx]
        else:
            preds += params[val]*all_preds[index][:, idx]
    
    param_sum = 0
    for key, val in params.items():
        param_sum += val
    
    preds = preds/param_sum    
    final_preds[:, idx] = preds

In [17]:
score, scores = get_score(labels, final_preds) 
print(score, scores)

0.44096085862233153 [0.46698225969736695, 0.43609804683466835, 0.40444852287626465, 0.4456389608409316, 0.45915490572403633, 0.43344245576072155]
